<a href="https://colab.research.google.com/github/unt-iialab/INFO5731_Spring2020/blob/master/Assignments/INFO5731_Assignment_Two.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

# **Question 1**

(20 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of the product [Apple iPhone 11](https://www.amazon.com/Apple-iPhone-11-64GB-Unlocked/dp/B07ZPKF8RG/ref=sr_1_13?dchild=1&keywords=iphone+12&qid=1631721363&sr=8-13) on amazon.

(2) Collect all User Reviews of the film [Shang-Chi and the Legend of the Ten Rings](https://www.imdb.com/title/tt9376612/reviews?ref_=tt_sa_3) from IMDB.

(3) Collect all the abstracts research papers by using the query [smart health](https://citeseerx.ist.psu.edu/search?q=natural+language+processing&submit.x=0&submit.y=0&sort=rlv&t=doc) from CiteSeerX.

(4) Collect the top 10,000 tweets by using hashtag ["#blacklivesmatter"](https://twitter.com/hashtag/blacklivesmatter) from Twitter with the following requirements: Location (Texas), Time frame (2021-01-01 to 2021-09-01). 


In [22]:
!apt-get update
!apt install chromium-chromedriver
!cp /usr/lib/chromium-browser/chromedriver /usr/bin
!pip install selenium
!pip install lxml

Hit:1 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease
Ign:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Ign:3 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release
Hit:5 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Get:6 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Hit:7 http://archive.ubuntu.com/ubuntu bionic InRelease
Hit:8 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease
Get:9 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Hit:11 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Hit:13 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu bionic InRelease
Get:14 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [74.6 kB]
Hit:15 http://ppa.launchpad.net/graph

In [126]:
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait as wait
from selenium.webdriver.common.by import By
from bs4 import BeautifulSoup
import string
import pandas as pd
import time, requests
import nltk
from nltk.probability import FreqDist
from textblob import TextBlob
from nltk.stem import PorterStemmer, WordNetLemmatizer
from spacy import displacy
import spacy

nlp=spacy.load("en_core_web_sm")
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [39]:
options = webdriver.ChromeOptions()
options.add_argument('-headless')
options.add_argument('-no-sandbox')
options.add_argument('-disable-dev-shm-usage')
driver = webdriver.Chrome('chromedriver',options=options)

In [40]:
def get_page(driver, url):
  driver.get(url)
  time.sleep(5)
  while True:
    try:
      driver.find_element_by_class_name("ipl-load-more__button").click()
      time.sleep(3)
    except: break
  print("Getting Spoiler Reviews")
  buttons = driver.find_elements_by_class_name("ipl-expander__container")
  return driver.page_source
print("Loading the Review page...")
web_page = get_page(driver, "https://www.imdb.com/title/tt9376612/reviews?ref_=tt_sa_3")
print("All reviews are loaded successfully")

Loading the Review page...


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:6: DeprecationWarning: find_element_by_* commands are deprecated. Please use find_element() instead
  


Getting Spoiler Reviews


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: DeprecationWarning: find_elements_by_* commands are deprecated. Please use find_elements() instead
  # Remove the CWD from sys.path while we load stuff.


All reviews are loaded successfully


In [41]:
soup = BeautifulSoup(web_page, "html.parser")

In [44]:
ratings = []
titles = []
reviews = []
review_container = soup.find_all("div", class_= "review-container")
for container in review_container:
  try: ratings.append(container.find("span", class_ = "rating-other-user-rating").text.replace("\n", ""))
  except: ratings.append("")

  try: titles.append(container.find("a", class_ = "title").text.replace("\n", ""))
  except: titles.append("")

  try: reviews.append(container.find("div", class_ = "text show-more__control").text)
  except: reviews.append("")


In [47]:
imdb_reviews = pd.DataFrame(zip(titles, ratings, reviews), columns=["Title", "Rating", "Review"])
imdb_reviews.to_csv("Scrapped IMDB Reviews.CSV", index = False)

# **Question 2**

(30 points) Here is a [legal case](https://github.com/unt-iialab/info5731-fall2021/blob/main/assignments/01-05-1%20%20Adams%20v%20Tanner.txt) we collected from westlaw, please follow the steps we mentioned in lesson 5 to clean the data:



(1) Basic feature extraction using text data

*   Number of sentences
*   Number of words
*   Number of characters
*   Average word length
*   Number of stopwords
*   Number of special characters
*   Number of numerics
*   Number of uppercase words

(2) Basic Text Pre-processing of text data

*   Lower casing
*   Punctuation removal
*   Stopwords removal
*   Frequent words removal
*   Rare words removal
*   Spelling correction
*   Tokenization
*   Stemming
*   Lemmatization

(3) Save all the **clean sentences** to a **csv file** (one column, each raw is a sentence) after finishing all the steps above.


(4) Advance Text Processing

*   Calculate the term frequency of all the terms.
*   Print out top 10 1-gram, top 10 2-grams, and top 10 3-grams terms as features.


In [52]:
file = requests.get("https://raw.githubusercontent.com/unt-iialab/info5731-fall2021/main/assignments/01-05-1%20%20Adams%20v%20Tanner.txt").text.replace("\r\n", "")

In [82]:
Number_of_sentences = len(file.split("."))
Number_of_words = len(file.split(" "))
Number_of_characters = len(file)
words_lengths = [len(word) for word in file.split(" ")]
Average_word_legth = sum(words_lengths)/len(words_lengths)
stopwords_list = nltk.corpus.stopwords.words("english")
Number_of_stopwords = len([word for word in nltk.tokenize.word_tokenize(file) if word in stopwords_list])
Number_of_special = len([syllab for syllab in file.split() if syllab in '[(_:/,#%\=@)]'])
Number_of_numaric = len([word for word in file.split() if word.isdigit()])
Number_of_uppercase = len([word for word in file.split() if word.isupper()])

In [84]:
print(f"""
Number of sentences: {Number_of_sentences}
Number of words: {Number_of_words}
Number of characters: {Number_of_characters}
Average word length: {Average_word_legth}
Number of stopwords: {Number_of_stopwords}
Number of special characters: {Number_of_special}
Number of numerics: {Number_of_numaric}
Number of uppercase words: {Number_of_uppercase}
""")


Number of sentences: 292
Number of words: 3575
Number of characters: 20295
Average word length: 4.677202797202797
Number of stopwords: 1727
Number of special characters: 8
Number of numerics: 28
Number of uppercase words: 62



In [89]:

punctuation_list = string.punctuation
# Lower the case
file_lower = file.lower()
# punctuation removal
file_r_punctuation = " ".join([word for word in nltk.tokenize.word_tokenize(file_lower) if word not in punctuation_list])
# stopwords_removal
file_r_stopwords = " ".join([word for word in nltk.tokenize.word_tokenize(file_r_punctuation) if word not in stopwords_list])


In [97]:
word_freq = dict(FreqDist(nltk.tokenize.word_tokenize(file_r_stopwords)))
# freq word removal
frq_list = list(sorted(word_freq.keys()))
file_r_freq= " ".join([word for word in nltk.tokenize.word_tokenize(file_r_punctuation) if word not in frq_list[:5]])

In [98]:
# rare word removal
file_r_rare= " ".join([word for word in nltk.tokenize.word_tokenize(file_r_freq) if word not in frq_list[-5:]])

In [100]:
# Spelling correction
file_corrected = TextBlob(file_r_rare).correct()

In [106]:
# tokenize
tokenize_words = nltk.tokenize.word_tokenize(str(file_corrected))

In [109]:
stemming = PorterStemmer()
lemmatizing = WordNetLemmatizer()
# Stemming
file_stem = [stemming.stem(word) for word in tokenize_words]
# Lemmatizer
file_lemminate = [lemmatizing.lemmatize(word) for word in tokenize_words]

In [111]:
print("Lemmatize Results\n", file_lemminate)
print("Stemmenize Results\n", file_stem)

Lemmatize Results
 ['5', 'all', '.', '740supreme', 'court', 'of', 'alabama.adams.manner', 'and', 'norton.june', 'term', '1843.synopsiswrit', 'of', 'error', 'to', 'the', 'circuit', 'court', 'of', 'sumter', 'west', 'headnotes', '2', '1', 'chattel', 'mortgagescropsa', 'growing', 'crop', 'ha', 'such', 'an', 'existence', 'a', 'to', 'be', 'the', 'subject-matter', 'of', 'a', 'mortgage', 'or', 'other', 'contract', 'which', 'pass', 'an', 'interest', 'to', 'vest', 'in', 'possession', 'either', 'immediately', 'or', 'at', 'a', 'future', 'time.4', 'case', 'that', 'cite', 'this', 'headnote', '2', 'creditor', 'remedieslien', 'and', 'priorityunder', 'st.1821', 'prohibiting', 'a', 'levy', 'on', 'a', 'crop', 'until', 'it', 'ha', 'been', 'gathered', 'no', 'line', 'attache', 'in', 'favor', 'of', 'a', 'i', 'a', 'on', 'a', 'growing', 'crop', 'nor', 'doe', 'such', 'line', 'attach', 'until', 'after', 'the', 'crop', 'ha', 'been', 'gathered.5', 'case', 'that', 'cite', 'this', 'headnote**1', 'this', 'wa', 'a', '

In [125]:
from collections import Counter
one_gram = list(nltk.ngrams(file_lemminate, n=1)) 
two_gram = list(nltk.ngrams(file_lemminate, n=2)) 
three_gram = list(nltk.ngrams(file_lemminate, n=3)) 

print("Top 10 1 grams\n, ", Counter(one_gram).most_common(10))
print("Top 10 2 grams\n, ", Counter(two_gram).most_common(10))
print("Top 10 3 grams\n, ", Counter(three_gram).most_common(10))

Top 10 1 grams
,  [(('the',), 334), (('of',), 142), (('to',), 117), (('a',), 111), (('it',), 88), (('and',), 83), (('in',), 81), (('that',), 56), (('wa',), 54), (('crop',), 51)]
Top 10 2 grams
,  [(('of', 'the'), 57), (('the', 'crop'), 25), (('to', 'the'), 23), (('the', 'claimant'), 22), (('that', 'the'), 20), (('it', 'is'), 17), (('in', 'execution'), 17), (('the', 'right'), 16), (('an', 'execution'), 16), (('in', 'the'), 16)]
Top 10 3 grams
,  [(('the', 'defendant', 'in'), 11), (('defendant', 'in', 'execution'), 11), (('the', 'right', 'to'), 10), (('the', 'circuit', 'court'), 8), (('of', 'the', 'crop'), 8), (('circuit', 'court', 'of'), 7), (('of', 'the', 'plaintiff'), 7), (('until', 'the', 'crop'), 7), (('right', 'to', 'levy'), 6), (('the', 'crop', 'is'), 6)]


# **Question 3**

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes: 

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

In [115]:
# Position tags
filtered_text = " ".join(file_lemminate)
text_pos_tags = nltk.pos_tag(filtered_text)
print(text_pos_tags)

[('5', 'CD'), (' ', 'VBZ'), ('a', 'DT'), ('l', 'NN'), ('l', 'NN'), (' ', 'NNP'), ('.', '.'), (' ', 'VB'), ('7', 'CD'), ('4', 'CD'), ('0', 'CD'), ('s', 'NN'), ('u', 'JJ'), ('p', 'NN'), ('r', 'NN'), ('e', 'NN'), ('m', 'NN'), ('e', 'NN'), (' ', 'NNP'), ('c', 'VBZ'), ('o', 'JJ'), ('u', 'JJ'), ('r', 'NN'), ('t', 'NN'), (' ', 'NNP'), ('o', 'VBZ'), ('f', 'JJ'), (' ', 'IN'), ('a', 'DT'), ('l', 'NN'), ('a', 'DT'), ('b', 'NN'), ('a', 'DT'), ('m', 'NN'), ('a', 'DT'), ('.', '.'), ('a', 'DT'), ('d', 'NN'), ('a', 'DT'), ('m', 'NN'), ('s', 'NN'), ('.', '.'), ('m', 'VB'), ('a', 'DT'), ('n', 'JJ'), ('n', 'NN'), ('e', 'NN'), ('r', 'NN'), (' ', 'VBZ'), ('a', 'DT'), ('n', 'JJ'), ('d', 'NN'), (' ', 'NNP'), ('n', 'NN'), ('o', 'NN'), ('r', 'NN'), ('t', 'NN'), ('o', 'NN'), ('n', 'NN'), ('.', '.'), ('j', 'NN'), ('u', 'JJ'), ('n', 'JJ'), ('e', 'NN'), (' ', 'NNP'), ('t', 'NN'), ('e', 'NN'), ('r', 'NN'), ('m', 'NN'), (' ', 'VBD'), ('1', 'CD'), ('8', 'CD'), ('4', 'CD'), ('3', 'CD'), ('.', '.'), ('s', 'VB'), ('y', 

In [118]:
Nouns = 0
Verbs = 0
Adjectives = 0
for word,tag in text_pos_tags:
  if tag[:2]=="NN": Nouns+=1
  elif tag[:2]=="JJ": Adjectives+=1
  elif tag[:2]=="VB": Verbs+=1
print("Number of Nouns: ", Nouns)
print("Number of Verbs", Verbs)
print("Number of Adjectives", Adjectives)

Number of Nouns:  12734
Number of Verbs 2449
Number of Adjectives 2169


In [129]:
# display depency parser
displacy.render(nlp(filtered_text),jupyter=True)

In [131]:

entity_types = ['PERSON','NORP','FAC','ORG','GPE','LOC','QUANTITY','ORDINAL','CARDINAL'
                'LANGUAGE','DATE','TIME','PERCENT','MONEY','PRODUCT','EVENT','WORK_OF_ART','LAW',]

entity_name = ['PERCENT','MONEY','QUANTITY','ORDINAL','CARDINAL','PRODUCT','EVENT','Title','LAW',
                'LANGUAGE','DATE','TIME','person','Nationality','Building','Institution','country','location']

def entity_(sentence):
    entity_lst = []
    text_ = nlp(sentence)
    for entit in text_.ents: entity_lst.append([entit.text, entit.label_])
    return entity_lst 

entities_ = entity_(filtered_text)
print("All Entitties\n")
print(entities_)

collect_ = Counter(entity for text_, entity in entities_)
print("Number og each entity\n")
print(collect_)

All Entitties

[['5', 'CARDINAL'], ['alabama.adams.manner', 'ORG'], ['2', 'CARDINAL'], ['1', 'CARDINAL'], ['chattel', 'ORG'], ['remedieslien', 'PERSON'], ['st.1821', 'PERSON'], ['doe', 'PERSON'], ['november 1840', 'DATE'], ['the circuit court', 'ORG'], ['allen harrison', 'PERSON'], ['thirty-seven hundred and seventy-seven', 'CARDINAL'], ['thirty', 'CARDINAL'], ['allen harrison', 'PERSON'], ['october 1839', 'DATE'], ['the twenty-second of may 1840', 'DATE'], ['button harrison', 'PERSON'], ['sumter county', 'GPE'], ['fourteen thousand dollar', 'MONEY'], ['one hundred and twenty acre', 'QUANTITY'], ['c. allen harrison', 'PERSON'], ['gainesville', 'GPE'], ['tennessee', 'GPE'], ['september 1840', 'DATE'], ['three', 'CARDINAL'], ['four', 'CARDINAL'], ['the first of september', 'DATE'], ['h. smith', 'PERSON'], ['1', 'CARDINAL'], ['may 1840', 'DATE'], ['2', 'CARDINAL'], ['1', 'CARDINAL'], ['361', 'CARDINAL'], ['1', 'CARDINAL'], ['307', 'CARDINAL'], ['east s', 'LOC'], ['604', 'CARDINAL'], ['joh

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):** 

In [ ]:
"""
Constituency parsing is more statistical parsing in which every sub phrase or postion tag is stored under thrit parent costituncey. 
by this we can find out relation between the terms in a sentence and their correspondence.

while dependency parsing is a graphical representation of relation between words under their postion tags
this gives us a arrow head indication of the depndent entities and group them together.
"""

# **Question 4**

(20 points) Python Regular Expression.

(1) Write a Python program to remove leading zeros from an IP address.

ip = "260.08.094.109"


(2) Write a Python Program to extract all the years from the following sentence.

sentence = "The 2010s were a dramatic decade, filled with ups and downs, more than 1000 stroies have happened. As the decade comes to a close, Insider took a look back at some of the biggest headline-grabbing stories, from 2010 to 2019. The result was 119 news stories that ranged from the heartwarming rescue of a Thai boys' soccer team from a flooded cave to the divisive election of President Donald Trump."

In [132]:
# Write your code here
ip = "260.08.094.109"
print("IP address\n", ".".join([str(int(i)) for i in ip.split(".")]))

IP address
 260.8.94.109


In [135]:
test = "The 2010s were a dramatic decade, filled with ups and downs, more than 1000 stroies have happened. As the decade comes to a close, Insider took a look back at some of the biggest headline-grabbing stories, from 2010 to 2019. The result was 119 news stories that ranged from the heartwarming rescue of a Thai boys' soccer team from a flooded cave to the divisive election of President Donald Trump."
entity_data = entity_(sentence=test)
years = [year for year,date in entity_data if date=='DATE'] 
print("Years:", years) 

Years: ['2010s', 'a dramatic decade', 'the decade', '2010 to 2019']
